In [12]:
from functools import cache
import pandas as pd

pd.set_option("display.max_columns", None)

In [13]:
@cache
def get_dataset_for(year):
    return pd.read_csv(f"datasets/sinac{year}DatosAbiertos.csv", dtype=object)

In [ ]:
_df = get_dataset_for(2013)

In [ ]:
estados_mexicanos = {
    "AGUASCALIENTES",
    "BAJA CALIFORNIA",
    "BAJA CALIFORNIA SUR",
    "CAMPECHE",
    "CHIAPAS",
    "CHIHUAHUA",
    "COAHUILA DE ZARAGOZA",
    "COLIMA",
    "DISTRITO FEDERAL",
    "DURANGO",
    "GUANAJUATO",
    "GUERRERO",
    "HIDALGO",
    "JALISCO",
    "MEXICO",
    "MICHOACAN DE OCAMPO",
    "MORELOS",
    "NAYARIT",
    "NUEVO LEON",
    "OAXACA",
    "PUEBLA",
    "QUERETARO  DE ARTEAGA",
    "QUINTANA ROO",
    "SAN LUIS POTOSI",
    "SINALOA",
    "SONORA",
    "TABASCO",
    "TAMAULIPAS",
    "TLAXCALA",
    "VERACRUZ DE IGNACIO DE LA LLAVE",
    "YUCATAN",
    "ZACATECAS",
}

In [ ]:
_df.sample(n=20)

In [ ]:
columns = [
    "ENTIDAD_NACMAD",
    "FECH_NACM",
    "ESTADO_CIVIL",
    "ENTIDAD_RESMAD",
    "NUMERO_EMBARAZOS",
    "NACIDOS_MUERTOS",
    "NACIDOS_VIVOS",
    "SOBREVIVIENTES",
    "ANTERIOR_NACIO",
    "VIVE_AUN",
    "ORDEN_NAC",
    "ATENCION_PRENA",
    "TRIMESTR_ATEN",
    "SOBREVIVIO_PARTO",
    "ESCOLARIDAD",
    "DESC_OCUPHAB",
    "OCUPACION_HABITUAL",
    "TRABAJA_ACTUALMENTE",
    "FECH_NACH",
    "HORA_NACH",
    "SEXO_RN",
    "GESTACH",
    "TALLAH",
    "PESOH",
    "APGARH",
    "SILVERMAN",
    "NACIMIENTOS",
    "MES_NACI",
    "Producto",
    "CIE10",
    "CIE10_2da",
    "PROCEDIMIENTO",
    "OTRO_PROCEDIMIENTO",
    "LUGAR_NACIM",
    "ENTIDAD_NACIM",
    "ENTIDAD_CERTIF",
    "FECHA_CERTIF",
]
columns = [x.lower() for x in columns]

In [ ]:
# len(set(columns) - set(df.columns.to_list()))

In [ ]:
# columns_original = get_dataset_for(2013).columns.to_list()
columns_selected = [
    "edo_captura",
    "edo_nac_madre",
    "fecha_nac_madre",
    "edad_madre",
    "estado_conyugal",
    "entidad_residencia_madre",
    "numero_embarazos",
    "hijos_nacidos_muertos",
    "hijos_nacidos_vivos",
    "hijos_sobrevivientes",
    "el_hijo_anterior_nacio",
    "vive_aun_hijo_anterior",
    "orden_nacimiento",
    "recibio_atencion_prenatal",
    "trimestre_recibio_primera_consulta",
    "total_consultas_recibidas",
    "madre_sobrevivio_al_parto",
    "escolaridad_madre",
    "ocupacion_habitual_madre",
    "trabaja_actualmente",
    "fecha_nacimiento_nac_vivo",
    "hora_nacimiento_nac_vivo",
    "sexo_nac_vivo",
    "semanas_gestacion_nac_vivo",
    "talla_nac_vivo",
    "peso_nac_vivo",
    "valoracion_apgar_nac_vivo",
    "valoracion_silverman_nac_vivo",
    "producto_de_un_embarazo",
    "codigo_anomalia",
    "anomalia_congenita_nac_vivo",
    "entidad_nacimiento",
    "entidad_certifico",
]
print(" - ", end="")
print(*sorted(columns_selected), sep="\n - ")
len(columns_selected)

In [ ]:
print("Año - #Cols - #Faltantes")
for year in range(2008, 2020):
    df = get_dataset_for(year)
    columns = set(df.columns.to_list())
    print(year, " - ", len(columns), " - ", len(set(columns_selected) - columns))

In [ ]:
df = pd.concat([get_dataset_for(year)[columns_selected] for year in range(2010, 2017)])

In [ ]:
df

In [ ]:
def _ano_nacimiento_vivo_func(str_date):
    try:
        return str_date.split("/")[-1]
    except:
        return ""


df["año_de_nacimiento_vivo"] = df["fecha_nacimiento_nac_vivo"].apply(
    _ano_nacimiento_vivo_func
)

In [ ]:
df.edad_madre = df.edad_madre.astype(int)
df = df[df.edad_madre < 120]

In [ ]:
df.info()

In [ ]:
set(df["año_de_nacimiento_vivo"].to_list())

In [ ]:
df_trisomias = df[df["codigo_anomalia"].apply(lambda x: "Q9" in x)]

In [ ]:
df_trisomias

In [ ]:
df_trisomias[["edad_madre"]].describe()

# Agrupación por estado lugar de nacimiento de la madre, y año del registro, agregación de edad de la madre

In [ ]:
consulta = df.groupby(["edo_captura", "edo_nac_madre", "año_de_nacimiento_vivo"]).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)

In [ ]:
[row_name for row_name in consulta.index.to_list() if row_name[0] == "JALISCO"]

In [ ]:
edos_fronterizos = {
    "BAJA CALIFORNIA",
    "SONORA",
    "CHIHUAHUA",
    "COAHUILA DE ZARAGOZA",
    "NUEVO LEON",
    "TAMAULIPAS",
}

In [ ]:
edo_nac_madre_de_interes = {
    "ESTADOS UNIDOS DE NORTEAMERICA",
    "OTROS PAISES",
}  # "OTROS PAISES DE LATINOAMERICA"}
consulta_edo_madre_especifico = consulta.loc[
    [
        row_name
        for row_name in consulta.index.to_list()
        if row_name[1] in edo_nac_madre_de_interes
        # and row_name[0] in edos_fronterizos
    ]
]

In [ ]:
# consulta_edo_madre_especifico.index, consulta_edo_madre_especifico.columns

In [ ]:
%matplotlib notebook
from matplotlib.figure import Figure

In [ ]:
{x[0] for x in consulta_edo_madre_especifico.index.to_list()}

In [ ]:
fig = Figure(figsize=(12, 6))
ax = fig.add_subplot()
edo_nac_madre_deseado = "ESTADOS UNIDOS DE NORTEAMERICA"
_df = consulta_edo_madre_especifico.reset_index()
edo = "BAJA CALIFORNIA"
for edo in {x[0] for x in consulta_edo_madre_especifico.index.to_list()}:
    _to_plot = _df[
        (_df["edo_nac_madre"] == edo_nac_madre_deseado) & (_df["edo_captura"] == edo)
    ][[("año_de_nacimiento_vivo", ""), ("edad_madre", "count")]]
    _to_plot.columns = ["Año", "Cantidad"]
    _to_plot = _to_plot.set_index("Año")

    _to_plot.plot(y="Cantidad", ax=ax, label=edo, linestyle="--", grid=True)

ax.legend(loc="upper left")
ax.set_xlabel("Año")
ax.set_ylabel("Cantidad de Nacimientos")
fig

In [ ]:
consulta_edo_madre_especifico.reset_index().columns

# Agrupación por estado de captura, y año

In [ ]:
# Edades de madres
consulta = df.groupby(["edo_captura", "año_de_nacimiento_vivo"]).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)
consulta2

In [ ]:
_df = consulta2.reset_index()
_df.columns = ["_".join(x).rstrip("_") for x in _df.columns.to_flat_index()]
_df = _df.rename(columns={"año_de_nacimiento_vivo": "año"})
_df

In [ ]:
fig = Figure(figsize=(12, 6))
ax = fig.add_subplot()
_df = consulta2.reset_index()
_df.columns = ["_".join(x).rstrip("_") for x in _df.columns.to_flat_index()]
_df = _df.rename(columns={"año_de_nacimiento_vivo": "año"})
edo = "BAJA CALIFORNIA"
for edo in estados_mexicanos:
    _to_plot = _df[(_df["edo_captura"] == edo)][
        ["año", "edad_madre_mean", "edad_madre_std"]
    ]
    _to_plot = _to_plot.set_index("año")
    _to_plot.plot(y="edad_madre_mean", ax=ax, label=edo, linestyle="--", grid=True)


fig

In [ ]:
fig = Figure(figsize=(12, 6))
ax = fig.add_subplot()
_df = consulta2.reset_index()
for edo in {x[0] for x in consulta.index.to_list()}:
    _to_plot = _df[(_df["edo_captura"] == edo)][
        [("año_de_nacimiento_vivo", ""), ("edad_madre", "count")]
    ]
    _to_plot.columns = ["Año", "Cantidad"]
    _to_plot = _to_plot.set_index("Año")

    _to_plot.plot(y="Cantidad", ax=ax, label=edo, linestyle="--", grid=True)

ax.legend(loc="upper left")
ax.set_xlabel("Año")
ax.set_ylabel("Cantidad de Nacimientos")
fig

# Filtrar a solo observar los:

## Top GDP

## Agrupación por zonas metropolitanas
